### 1 背景
 ### 有一批交易数据，数据总量达到28万条。其中正常交易数据量占比99.83%，欺诈交易数据仅占0.17%，此案例属于典型的不平衡数据案例
 ### 2 目标
 ### 训练出一个模型，能够判断出欺诈交易数据。
 ### 方案三：
 ### 基于pytorch的DL(深度学习）解决方法

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import time
import warnings
warnings.filterwarnings('ignore')

In [6]:
import os

abs_path = os.path.abspath('.')
current_path = abs_path + '/tmp/pycharm_project_317/pytorch_dl/'
credits_data_path = current_path + 'creditcard.csv'

In [8]:
# 加载数据文件
df = pd.read_csv(credits_data_path)
df.head()

Time        V1        V2        V3        V4        V5        V6        V7  \
0   0.0 -1.359807 -0.072781  2.536347  1.378155 -0.338321  0.462388  0.239599   
1   0.0  1.191857  0.266151  0.166480  0.448154  0.060018 -0.082361 -0.078803   
2   1.0 -1.358354 -1.340163  1.773209  0.379780 -0.503198  1.800499  0.791461   
3   1.0 -0.966272 -0.185226  1.792993 -0.863291 -0.010309  1.247203  0.237609   
4   2.0 -1.158233  0.877737  1.548718  0.403034 -0.407193  0.095921  0.592941   

         V8        V9  ...       V21       V22       V23       V24       V25  \
0  0.098698  0.363787  ... -0.018307  0.277838 -0.110474  0.066928  0.128539   
1  0.085102 -0.255425  ... -0.225775 -0.638672  0.101288 -0.339846  0.167170   
2  0.247676 -1.514654  ...  0.247998  0.771679  0.909412 -0.689281 -0.327642   
3  0.377436 -1.387024  ... -0.108300  0.005274 -0.190321 -1.175575  0.647376   
4 -0.270533  0.817739  ... -0.009431  0.798278 -0.137458  0.141267 -0.206010   

        V26       V27       V28  Amount  Class  
0 -0.189115  0.133558 -0.021053  149.62      0  
1  0.125895 -0.008983  0.014724    2.69      0  
2 -0.139097 -0.055353 -0.059752  378.66      0  
3 -0.221929  0.062723  0.061458  123.50      0  
4  0.502292  0.219422  0.215153   69.99      0  

[5 rows x 31 columns]

In [10]:
# 数据表中的大多数列的数据已经归一化，接下来对Amount进行归一化
from sklearn.preprocessing import StandardScaler

df['scaled_amount'] = StandardScaler().fit_transform(df['Amount'].values.reshape(-1,1)) # 金额归一化
df['scaled_time'] = StandardScaler().fit_transform(df['Time'].values.reshape(-1,1)) # 时间归一化

df.drop(['Amount', 'Time'], axis=1, inplace=True) # 删除原始的数据列

In [11]:
x = df.drop('Class', axis=1) #数据集
y = df['Class'] #标签

print("x shape :", x.shape)
print('y shape :', y.shape)

x shape : (284807, 30)
y shape : (284807,)


In [40]:
# 数据集分离：Train 和 Test
from sklearn.model_selection import train_test_split

x_new_train, x_new_test, y_new_train, y_new_test = train_test_split(x, y, test_size=0.1, random_state=666)

In [69]:
# 数据类型转换：DataFrame ---> array ---> Tensor
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optimizer

train = torch.utils.data.TensorDataset(torch.tensor(x_new_train.values).float(),
                                         torch.tensor(y_new_train.values).float())

val = torch.utils.data.TensorDataset(torch.tensor(x_new_test.values).float(),
                                       torch.tensor(y_new_test.values).float())

# 另一种写法
# X_train = torch.from_numpy(X_new_train.values)
# y_train = torch.from_numpy(y_new_train.values)
# train = torch.utils.data.TensorDataset(X_train, y_train)

# X_val = torch.from_numpy(X_new_test.values)
# y_val = torch.from_numpy(y_new_test.values)
# val = torch.utils.data.TensorDataset(X_val, y_val)
type(train)

torch.utils.data.dataset.TensorDataset

In [70]:
# 一批一批地读取数据
batch_size = 64

train_dataloader = torch.utils.data.DataLoader(train, batch_size=batch_size)

val_dataloader = torch.utils.data.DataLoader(val, batch_size=batch_size)
type(train_dataloader)

torch.utils.data.dataloader.DataLoader

In [85]:
# 自定义3层隐藏层的网络
class Model(torch.nn.Module):
    def __init__(self, input_dim=30, hidden_unit=16):
        super(Model, self).__init__()
        self.fc1 = torch.nn.Linear(input_dim, hidden_unit) # 输入: 30 , 有30个特征
        self.fc2 = torch.nn.Linear(hidden_unit, 18)
        self.fc3 = torch.nn.Linear(18, 20)
        self.relu = torch.nn.ReLU()
        self.fc4 = torch.nn.Linear(20, 24)
        self.fc5 = torch.nn.Linear(24, 1) # 输出：1， 一个结果，是否欺诈

    def forward(self, x):
        x = self.relu(self.fc1(x))
        x = self.relu(self.fc2(x))
        x = F.dropout(x, p=0.25)
        x = self.relu(self.fc3(x))
        x = self.relu(self.fc4(x))
        x = F.sigmoid(self.fc5(x))
        print('x.shape = ', x.shape)
        return x

In [86]:
input_dim = x_new_train.shape[1] # 列数

hidden_unit = 16 # 16个隐藏单元

epochs = 10 # 运行多少轮

model = Model(input_dim, hidden_unit) # 创建模型

loss = torch.nn.BCELoss() # 损失函数

learning_rate = 0.003 # 学习率

optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)

In [95]:
# 定义训练函数
def train(epochs, model, loss_func, optimizer, train_loader):
    for epoch in range(epochs):
        model.train() # 模型训练
        for (i, train) in enumerate(train_loader):
            # print(type(i))
            # print(type(train))
            X, y = train # 获取训练数据和标签
            # print(X.shape)
            # print(y.shape)
            y_pred = model(X) # 预测
            y_pred = y_pred.squeeze(-1) # ValueError: Using a target size (torch.Size([64])) that is different to the input size (torch.Size([64, 1])) is deprecated. Please ensure they have the same size.
            # print(y_pred.shape)
            loss = loss_func(y_pred, y) # 计算损失
            optimizer.zero_grad() # 重置梯度
            loss.backward() # 反向传播
            optimizer.step() # 更新参数
            print('epoch : {}, batch : {}, Loss : {}'.format(epoch, i, loss.item()) )# 输出损失

In [96]:
train(epochs, model, loss, optimizer, train_dataloader) # 训练

x.shape =  torch.Size([64, 1])
epoch : 0, batch : 0, Loss : 8.671812975080684e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 1, Loss : 0.00010730560461524874
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 2, Loss : 0.003385096788406372
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 3, Loss : 5.5194950618897565e-06
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 4, Loss : 4.881065615336411e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 5, Loss : 5.962020077276975e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 6, Loss : 6.649504211964086e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 7, Loss : 1.2007716577500105e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 8, Loss : 0.00010569524602033198
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 9, Loss : 1.8508080756873824e-05
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 10, Loss : 3.355783064762363e-06
x.shape =  torch.Size([64, 1])
epoch : 0, batch : 11, Loss : 3.302657660242403e-06
x.shape = 

In [98]:
# 定义验证函数
def val(model, val_loader):
    correct = 0
    total = 0
    model.eval()
    with torch.no_grad():
        for data in val_loader:
            inputs, labels = data
            outputs = model(inputs)
            # _,predicted = torch.max(outputs.data, 1)
            # total += labels.size()
            # correct += (predicted == labels).sum().item()
            pred = outputs.argmax(dim=1, keepdim=True)
            correct += pred.eq(labels.view_as(pred)).sum().item()

    print("Accurary {}% ".format(100 * correct / len(val_loader.dataset)))

In [99]:
val(model, val_dataloader)

x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape =  torch.Size([64, 1])
x.shape 